# Loading the data

In [ ]:
import pandas as pd
import glob
import numpy as np
import altair as alt
import json
import math


def importAll(path):    
    all_files = glob.glob(path + "/*.csv")
    res = {}

    for filename in all_files:
        print('Importing:', filename)
        df = pd.read_csv(filename, index_col=None, header=0)
        res[filename] = df
    return res
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 40)

In [ ]:
competitive = importAll('1076')

# Taking an inital look at the data

In [ ]:
competitive_datasets = list(competitive.keys())
competitive_datasets

In [ ]:
matchdata = competitive['1076/LeagueofLegends.csv']
#indendepent variables
print(matchdata.columns)
matchdata.describe()
#blue side wins 5% more than red side!

In [ ]:
wins = competitive['1076/matchinfo.csv']
#dependent (winning)
wins.head()
wins.columns

In [234]:
wins = wins[['League', 'Year', 'Season', 'Type', 'blueTeamTag', 'bResult', 'rResult',
       'redTeamTag', 'gamelength']]
matchdata = matchdata[[ 'golddiff', 'goldblue', 'bKills', 'bTowers', 'bInhibs', 'bDragons',
       'bBarons', 'bHeralds', 'goldred', 'rKills', 'rTowers', 'rInhibs',
       'rDragons', 'rBarons', 'rHeralds', 'blueTop', 'blueTopChamp',
       'goldblueTop', 'blueJungle', 'blueJungleChamp', 'goldblueJungle',
       'blueMiddle', 'blueMiddleChamp', 'goldblueMiddle', 'blueADC',
       'blueADCChamp', 'goldblueADC', 'blueSupport', 'blueSupportChamp',
       'goldblueSupport', 'blueBans', 'redTop', 'redTopChamp', 'goldredTop',
       'redJungle', 'redJungleChamp', 'goldredJungle', 'redMiddle',
       'redMiddleChamp', 'goldredMiddle', 'redADC', 'redADCChamp',
       'goldredADC', 'redSupport', 'redSupportChamp', 'goldredSupport',
       'redBans']]
wins.shape[0] == matchdata.shape[0]
#wins dataset has one to one correspondence to matchdata
league = pd.concat([wins, matchdata], axis=1)
league.columns

Index(['League', 'Year', 'Season', 'Type', 'blueTeamTag', 'bResult', 'rResult',
       'redTeamTag', 'gamelength', 'golddiff', 'goldblue', 'bKills', 'bTowers',
       'bInhibs', 'bDragons', 'bBarons', 'bHeralds', 'goldred', 'rKills',
       'rTowers', 'rInhibs', 'rDragons', 'rBarons', 'rHeralds', 'blueTop',
       'blueTopChamp', 'goldblueTop', 'blueJungle', 'blueJungleChamp',
       'goldblueJungle', 'blueMiddle', 'blueMiddleChamp', 'goldblueMiddle',
       'blueADC', 'blueADCChamp', 'goldblueADC', 'blueSupport',
       'blueSupportChamp', 'goldblueSupport', 'blueBans', 'redTop',
       'redTopChamp', 'goldredTop', 'redJungle', 'redJungleChamp',
       'goldredJungle', 'redMiddle', 'redMiddleChamp', 'goldredMiddle',
       'redADC', 'redADCChamp', 'goldredADC', 'redSupport', 'redSupportChamp',
       'goldredSupport', 'redBans'],
      dtype='object')

# Transforming the data 

## (no cleaning necessary, data was preprocessed before hand by Kaggle contributor)

In [236]:

'max(goldblue)'
'max(goldred)'
'len(bKills)'
'len(bDragons)'
'len(bBarons)'
'len(rDragons)'
'get last of all columns starting with gold'
'get gold amt at early, mid, and late game for each role'
'if game was comeback, even, or one sided (looking at shifts in gold diff)'
TIMES = [(0, 'early'), (1, 'mid'), (2, 'late')]
OBJECTIVES = ['Kills', 'Towers', 'Inhibs', 'Dragons', 'Barons', 'Heralds']
def getGold(name):
    totalgoldblue = []
    for x in league['gold'+name]:
        x = json.loads(x)
        totalgoldblue.append(int(x[-1]))
    return totalgoldblue

def getTimedGold(name, t):
    totalgoldblue = []
    for x in league['gold'+name]:
        x = json.loads(x)
        total = len(x) // 3        
        step = total // 2 + t * total #break at 16%, 49%, 83%
        avg = round((int(x[step-1]) + int(x[step]) + int(x[step+1])) / 3)
        totalgoldblue.append(avg)
    return totalgoldblue

def getNum(name):
    totalgoldblue = []
    for i,x in enumerate(league[name]):                
        numOccurences = list(x).count('[') -1
        # if name == 'bHeralds' and numOccurences > 2:
        #     print(league.iloc[i, :])

        totalgoldblue.append(numOccurences)
    return totalgoldblue


def buildQuantative():
    categorical = wins[['League', 'Year', 'Season', 'Type']]    
    quantleague = wins[['gamelength']]    
    #independent
    for c in ['blue', 'red']:
        quantleague['totalgold'+c] = getGold(c)
        for t in TIMES:        
            quantleague[t[1]+'gold'+c] = getTimedGold(c, t[0])
    for c in ['b', 'r']:
        for o in OBJECTIVES:
            quantleague[c+o] = getNum(c+o)
    quantleague['bluewin'] = wins[['bResult']] 

    #dependent variables
    quantleague = pd.concat([quantleague, pd.get_dummies(categorical)], axis=1)
    return quantleague


quantleague = buildQuantative()
#this is what we'll use for doing predictions on later!

quantleague.describe()

# quantleague = pd.DataFrame()
# league



gamelength  totalgoldblue  earlygoldblue   midgoldblue   lategoldblue  \
count  7620.000000    7620.000000    7620.000000   7620.000000    7620.000000   
mean     37.012598   62858.331890    8299.484383  28131.820604   50194.975984   
std       7.983238   14964.594618    2062.401976   7105.323666   12252.914241   
min      17.000000   24795.000000    3074.000000  10817.000000   18859.000000   
25%      31.000000   52737.750000    6984.000000  23245.750000   41656.250000   
50%      36.000000   61403.000000    8004.000000  27083.000000   48585.500000   
75%      41.000000   71411.750000    9377.000000  31978.000000   56858.500000   
max      95.000000  177698.000000   24252.000000  78494.000000  145273.000000   

        totalgoldred  earlygoldred    midgoldred    lategoldred       bKills  \
count    7620.000000   7620.000000   7620.000000    7620.000000  7620.000000   
mean    62012.024147   8276.117585  27921.372572   49726.788451    25.801050   
std     15831.233725   2065.197409   7213.266262   12735.605451    13.537435   
min     22880.000000   3614.000000  10214.000000   17591.000000     0.000000   
25%     50890.750000   6948.000000  22967.000000   40725.500000    16.000000   
50%     60886.000000   8034.500000  26991.500000   48560.000000    26.000000   
75%     71274.000000   9361.000000  31853.500000   56923.250000    34.000000   
max    173712.000000  24082.000000  90926.000000  141750.000000   142.000000   

           bTowers      bInhibs     bDragons      bBarons     bHeralds  \
count  7620.000000  7620.000000  7620.000000  7620.000000  7620.000000   
mean      6.745669     1.231627     1.853937     0.724934     0.325591   
std       3.622223     1.360968     1.365986     0.749805     0.534811   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%       3.000000     0.000000     1.000000     0.000000     0.000000   
50%       8.000000     1.000000     2.000000     1.000000     0.000000   
75%      10.000000     2.000000     3.000000     1.000000     1.000000   
max      16.000000    14.000000     8.000000     5.000000     3.000000   

            rKills      rTowers      rInhibs     rDragons      rBarons  \
count  7620.000000  7620.000000  7620.000000  7620.000000  7620.000000   
mean     24.318635     5.939108     1.015354     1.923622     0.731102   
std      14.165589     3.775039     1.311514     1.438577     0.820721   
min       0.000000     0.000000     0.000000     0.000000     0.000000   
25%      12.000000     2.000000     0.000000     1.000000     0.000000   
50%      24.000000     6.000000     1.000000     2.000000     1.000000   
75%      34.000000    10.000000     2.000000     3.000000     1.000000   
max      98.000000    14.000000    14.000000     7.000000     6.000000   

          rHeralds      bluewin         Year  League_CBLoL   League_CLS  \
count  7620.000000  7620.000000  7620.000000   7620.000000  7620.000000   
mean      0.247638     0.544094  2016.280971      0.039501     0.022966   
std       0.486288     0.498085     0.848200      0.194797     0.149805   
min       0.000000     0.000000  2014.000000      0.000000     0.000000   
25%       0.000000     0.000000  2016.000000      0.000000     0.000000   
50%       0.000000     1.000000  2016.000000      0.000000     0.000000   
75%       0.000000     1.000000  2017.000000      0.000000     0.000000   
max       3.000000     1.000000  2018.000000      1.000000     1.000000   

       League_EULCS   League_IEM   League_LCK   League_LCL   League_LJL  \
count   7620.000000  7620.000000  7620.000000  7620.000000  7620.000000   
mean       0.144226     0.018110     0.189633     0.036877     0.033858   
std        0.351342     0.133359     0.392036     0.188471     0.180876   
min        0.000000     0.000000     0.000000     0.000000     0.000000   
25%        0.000000     0.000000     0.000000     0.000000     0.000000   
50%        0.000000     0.000000     0.000000     0.000000     0.000000   
75%        0.000000   

# Exploratory analysis

In [237]:
# Doing a variety of groupbys to find any interesting characteristics across our dependent variables
tidyleague = pd.concat([ wins[['League', 'Year', 'Season', 'Type']]  ,quantleague.drop('Year', axis=1)], axis=1)
grouped = {}
def groupby(column):
    return tidyleague.groupby(column).agg(np.mean).reset_index()        

for col in ['League', 'Year', 'Season', 'Type']:    
    grouped[col] = groupby(col)
grouped['Type']

# which teams were the best
# gold difference vs winning probability
# gamelength and winning
# kils and winning
# how different seasons affected monsters killed, gamelength
# neutral objectives and winning
# groupby league and year
#grouby teams (find playstyles)
#season vs playoff




Type         Year  gamelength  totalgoldblue  earlygoldblue  \
0  International  2015.916413   36.545593   62180.089666    8106.699088   
1       Playoffs  2016.179355   36.832258   62193.574194    8239.470968   
2      Promotion  2016.329923   37.677749   62465.322251    8270.524297   
3       Regional  2015.979021   37.132867   63052.979021    8246.041958   
4         Season  2016.341589   37.042632   63050.672740    8333.506811   

    midgoldblue  lategoldblue  totalgoldred  earlygoldred    midgoldred  \
0  27771.764438  49546.451368  61149.803951   8094.392097  27503.606383   
1  27909.236129  49815.166452  61515.854194   8220.291613  27710.910968   
2  28065.751918  50082.355499  62370.025575   8285.974425  28042.941176   
3  28113.391608  50357.000000  61832.531469   8180.552448  27839.790210   
4  28209.281797  50326.224306  62160.186450   8306.659296  27992.508403   

    lategoldred     bKills   bTowers   bInhibs  bDragons   bBarons  bHeralds  \
0  48943.344985  26.990881  6.723404  1.258359  1.873860  0.732523  0.249240   
1  49392.130323  26.376774  6.683871  1.227097  1.821935  0.725161  0.330323   
2  49999.790281  24.936061  6.534527  1.104859  1.774936  0.687980  0.286445   
3  49770.412587  24.349650  6.629371  1.181818  1.867133  0.692308  0.188811   
4  49843.873872  25.680170  6.774279  1.239165  1.861136  0.727401  0.339996   

      rKills   rTowers   rInhibs  rDragons   rBarons  rHeralds   bluewin  \
0  25.294833  5.765957  0.969605  1.876900  0.697568  0.218845  0.556231   
1  25.091613  5.889032  0.922581  1.874839  0.686452  0.242581  0.539355   
2  24.976982  6.107417  1.074169  2.089514  0.767263  0.176471  0.514066   
3  23.426573  5.720280  0.937063  1.664336  0.783217  0.139860  0.538462   
4  24.076066  5.960021  1.031311  1.930833  0.737308  0.259331  0.545551   

   League_CBLoL  League_CLS  League_EULCS  League_IEM  League_LCK  League_LCL  \
0      0.000000    0.000000      0.000000    0.209726    0.000000    0.000000   
1      0.074839    0.029677      0.187097    0.000000    0.098065    0.068387   
2      0.000000    0.000000      0.352941    0.000000    0.186701    0.000000   
3      0.000000    0.000000      0.230769    0.000000    0.272727    0.000000   
4      0.042986    0.026888      0.138511    0.000000    0.222360    0.040333   

   League_LJL  League_LLN  League_LMS  League_MSI  League_NALCS  League_OPL  \
0    0.000000    0.000000    0.000000    0.168693      0.000000    0.000000   
1    0.014194    0.025806    0.085161    0.000000      0.181935    0.070968   
2    0.000000    0.000000    0.109974    0.000000      0.350384    0.000000   
3    0.000000    0.000000    0.251748    0.000000      0.244755    0.000000   
4    0.043694    0.039271    0.111976    0.000000      0.169644    0.071290   

   League_RR  League_TCL  League_WC  Season_Spring  Season_Summer  \
0   0.153495    0.000000   0.468085       0.275076       0.724924   
1   0.000000    0.163871   0.000000       0.512258       0.487742   
2   0.000000    0.000000   0.000000       0.634271       0.365729   
3   0.000000    0.000000   0.000000       0.000000       1.000000   
4   0.000000    0.093048   0.000000       0.475146       0.524854   

   Type_International  Type_Playoffs  Type_Promotion  Type_Regional  \
0                 1.0            0.0             0.0            0.0   
1                 0.0            1.0             0.0            0.0   
2                 0.0            0.0             1.0            0.0   
3                 0.0            0.0             0.0            1.0   
4                 0.0            0.0             0.0            0.0   

   Type_Season  
0          0.0  
1          0.0  
2          0.0  
3          0.0  
4          1.0

In [238]:
grouped['Season']

Season         Year  gamelength  totalgoldblue  earlygoldblue  \
0  Spring  2016.387813   37.118736   63190.918850    8330.932232   
1  Summer  2016.189630   36.921860   62573.997566    8272.599075   

    midgoldblue  lategoldblue  totalgoldred  earlygoldred    midgoldred  \
0  28279.965547  50481.394077  62211.538155   8316.504271  28052.120729   
1  28005.168939  49950.112220  61841.456183   8241.590312  27809.593720   

    lategoldred     bKills   bTowers  bInhibs  bDragons   bBarons  bHeralds  \
0  49930.296982  26.137813  6.764806  1.23918  1.860194  0.709852  0.318907   
1  49552.805501  25.513145  6.729309  1.22517  1.848588  0.737829  0.331305   

      rKills   rTowers   rInhibs  rDragons   rBarons  rHeralds   bluewin  \
0  24.535308  5.907460  1.019932  1.974089  0.698178  0.248007  0.548690   
1  24.133398  5.966164  1.011441  1.880477  0.759250  0.247322  0.540166   

   League_CBLoL  League_CLS  League_EULCS  League_IEM  League_LCK  League_LCL  \
0      0.045843    0.022210      0.150057    0.019932    0.194476    0.040148   
1      0.034080    0.023612      0.139241    0.016553    0.185492    0.034080   

   League_LJL  League_LLN  League_LMS  League_MSI  League_NALCS  League_OPL  \
0    0.042141    0.033884    0.096241    0.031606      0.167426    0.066913   
1    0.026777    0.029942    0.107108    0.000000      0.166504    0.054284   

   League_RR  League_TCL  League_WC  Season_Spring  Season_Summer  \
0   0.000000    0.089123   0.000000            1.0            0.0   
1   0.024586    0.082765   0.074976            0.0            1.0   

   Type_International  Type_Playoffs  Type_Promotion  Type_Regional  \
0            0.051538       0.113041        0.070615        0.00000   
1            0.116115       0.092016        0.034810        0.03481   

   Type_Season  
0     0.764806  
1     0.722249

In [239]:
grouped['Year']
#Hmm...Heralds seem like a dead giveaway as they weren't introduced in 2014...the blue win percentage is also much higher that year! (The rift herald is easier to reach by redside)
#Baron kills definitely increase over time!

Year  gamelength  totalgoldblue  earlygoldblue   midgoldblue  lategoldblue  \
0  2014   36.653846   57765.423077    7329.269231  25790.346154  45832.000000   
1  2015   38.331551   60451.748663    8085.742647  27363.474599  48429.720588   
2  2016   37.040096   63541.856055    8476.791901  28455.668003  50807.599840   
3  2017   36.358502   63178.429477    8237.482936  28137.199034  50332.497735   
4  2018   37.643154   67974.278008    8957.228216  30233.883817  54335.705394   

   totalgoldred  earlygoldred    midgoldred   lategoldred     bKills  \
0  56518.653846   7305.102564  25354.179487  45043.358974  29.871795   
1  59688.325535   8079.409091  27202.130348  48090.004679  28.665775   
2  63058.649559   8475.852045  28379.006415  50555.714515  24.182839   
3  62074.948656   8187.744186  27802.768952  49676.757475  26.015705   
4  66518.701245   8958.614108  30110.522822  53512.045643  20.497925   

    bTowers   bInhibs  bDragons   bBarons  bHeralds     rKills   rTowers  \
0  6.833333  1.371795  2.153846  0.628205  0.000000  27.410256  5.564103   
1  6.772727  1.179813  2.176471  0.709893  0.002674  27.033422  5.979947   
2  6.657177  1.161989  1.855253  0.672815  0.502406  23.587009  6.136327   
3  6.797342  1.298097  1.715494  0.761401  0.335246  24.021142  5.792208   
4  6.755187  1.315353  1.643154  0.887967  0.473029  18.124481  5.784232   

    rInhibs  rDragons   rBarons  rHeralds   bluewin  League_CBLoL  League_CLS  \
0  1.064103  1.833333  0.679487  0.000000  0.589744      0.000000    0.000000   
1  0.955214  2.143717  0.710561  0.003342  0.546791      0.000000    0.000000   
2  1.022855  1.990377  0.693665  0.426624  0.528067      0.058540    0.000000   
3  1.025068  1.786771  0.764422  0.225008  0.553307      0.041075    0.050438   
4  1.161826  1.775934  0.804979  0.302905  0.551867      0.078838    0.033195   

   League_EULCS  League_IEM  League_LCK  League_LCL  League_LJL  League_LLN  \
0      0.000000    0.000000    0.000000    0.000000    0.000000     0.00000   
1      0.199866    0.031417    0.262701    0.000000    0.000000     0.00000   
2      0.143545    0.026063    0.193264    0.056135    0.043705     0.00000   
3      0.121413    0.007853    0.152522    0.042585    0.045002     0.07309   
4      0.165975    0.000000    0.269710    0.000000    0.000000     0.00000   

   League_LMS  League_MSI  League_NALCS  League_OPL  League_RR  League_TCL  \
0    0.000000    0.000000      0.000000    0.000000   0.000000    0.000000   
1    0.131684    0.018717      0.205214    0.000000   0.000000    0.101604   
2    0.104250    0.016439      0.154370    0.087410   0.000000    0.085405   
3    0.086681    0.012685      0.163395    0.067351   0.030504    0.081244   
4    0.141079    0.000000      0.161826    0.070539   0.000000    0.078838   

   League_WC  Season_Spring  Season_Summer  Type_International  Type_Playoffs  \
0   1.000000       0.000000       1.000000            1.000000       0.000000   
1   0.048797       0.440508       0.559492            0.098930       0.122326   
2   0.030874       0.430233       0.569767            0.073376       0.108260   
3   0.024162       0.464814       0.535186            0.075204       0.097252   
4   0.000000       1.000000       0.000000            0.000000       0.000000   

   Type_Promotion  Type_Regional  Type_Season  
0        0.000000       0.000000     0.000000  
1        0.088235       0.033422     0.657086  
2        0.027265       0.018444     0.772654  
3        0.036545       0.014195     0.776805  
4        0.290456       0.000000     0.709544

In [240]:
grouped["League"]
#This one seems the most promising!

League         Year  gamelength  totalgoldblue  earlygoldblue  \
0   CBLoL  2016.578073   39.777409   68018.568106    8972.368771   
1     CLS  2017.045714   35.480000   61399.434286    8057.845714   
2   EULCS  2016.166515   36.941765   62394.008189    8330.469518   
3     IEM  2015.847826   35.702899   60974.101449    7950.753623   
4     LCK  2016.167474   38.811765   65798.914187    8737.622145   
5     LCL  2016.501779   36.491103   62455.604982    8186.530249   
6     LJL  2016.577519   36.670543   61590.554264    8203.019380   
7     LLN  2017.000000   35.462810   61067.892562    7983.214876   
8     LMS  2016.203085   36.696658   61945.326478    8187.208226   
9     MSI  2016.126126   35.720721   61768.297297    8055.315315   
10  NALCS  2016.245283   36.956761   62571.672170    8266.640723   
11    OPL  2016.561135   34.375546   59493.683406    7730.899563   
12     RR  2017.000000   36.801980   63960.900990    8422.009901   
13    TCL  2016.237366   36.026034   61172.278714    8027.117917   
14     WC  2015.516234   37.136364   62284.873377    8091.691558   

     midgoldblue  lategoldblue  totalgoldred  earlygoldred    midgoldred  \
0   30424.285714  54401.388704  67405.372093   9024.674419  30424.807309   
1   27281.462857  48966.217143  60728.331429   7941.320000  26786.200000   
2   28151.124659  49840.092812  61719.245678   8282.355778  27920.483167   
3   26994.934783  48530.340580  60157.956522   7987.557971  26940.528986   
4   29493.244291  52608.040138  64726.935640   8716.918339  29325.875433   
5   27818.967972  49879.096085  61571.131673   8164.572954  27582.249110   
6   27585.895349  49241.007752  61806.748062   8158.120155  27568.344961   
7   26923.185950  48552.838843  60056.900826   7944.958678  26921.904959   
8   27662.365039  49467.937018  60964.715938   8147.961440  27320.719794   
9   27616.369369  49027.459459  59278.810811   7975.972973  26846.990991   
10  28108.951258  49994.463836  61630.358491   8233.161164  27850.632075   
11  26325.194323  47366.248908  59300.218341   7735.969432  26202.585153   
12  28664.138614  51058.059406  64684.178218   8447.376238  28863.148515   
13  27289.915773  48858.526799  60112.467075   8050.540582  27100.886677   
14  27883.198052  49693.071429  61109.490260   8069.185065  27546.707792   

     lategoldred     bKills   bTowers   bInhibs  bDragons   bBarons  bHeralds  \
0   54166.073090  24.192691  7.046512  1.468439  2.109635  0.794020  0.448505   
1   48173.045714  27.942857  6.634286  1.102857  1.794286  0.668571  0.394286   
2   49565.073703  25.497725  6.821656  1.202002  1.868062  0.758872  0.320291   
3   48079.789855  29.333333  6.500000  1.181159  1.789855  0.594203  0.246377   
4   52167.652595  23.278893  6.741176  1.296886  2.016609  0.766090  0.301730   
5   49351.277580  27.316726  6.697509  1.120996  1.654804  0.626335  0.419929   
6   49194.674419  23.317829  6.232558  1.058140  1.635659  0.674419  0.399225   
7   48147.954545  24.958678  6.739669  1.400826  1.578512  0.681818  0.322314   
8   48741.800771  25.262211  6.493573  1.115681  1.848329  0.706941  0.331620   
9   47698.810811  28.756757  6.792793  1.108108  2.072072  0.792793  0.360360   
10  49394.905660  26.415094  6.915881  1.255503  1.880503  0.720126  0.277516   
11  47240.294760  27.799127  6.478166  1.085153  1.517467  0.620087  0.441048   
12  51601.960396  25.584158  6.405941  1.168317  1.683168  0.801980  0.415842   
13  48278.140888  29.546708  6.923430  1.283308  1.813170  0.735069  0.326187   
14  48906.961039  25.766234  6.902597  1.376623  1.902597  0.750000  0.155844   

       rKills   rTowers   rInhibs  rDragons   rBarons  rHeralds   bluewin  \
0   22.750831  6.215947  1.239203  2.089701  0.770764  0.415282  0.544850   
1   25.942857  6.022857  1.068571  1.811429  0.760000  0.262857  0.525714   
2   24.252957  6.189263  1.047316  1.837125  0.744313  0.247498  0.535942   
3   27.231884  5.615942  0.920290  1.775362  0.666667  0.195652  0.550725   
4   21.645675  

In [254]:
bDB = alt.Chart(grouped['League']).mark_point(color="blue").encode(
    x=alt.X('bDragons', scale=alt.Scale(zero=False)),
    y=alt.Y('bBarons', scale=alt.Scale(zero=False)),
    
)
bDB + alt.Chart(grouped['League']).mark_point(color="red").encode(
    x=alt.X('rDragons', scale=alt.Scale(zero=False)),
    y=alt.Y('rBarons', scale=alt.Scale(zero=False))    
)




alt.LayerChart(...)

In [264]:
alt.Chart(tidyleague.sample(5000)).mark_point(size=.3).encode(
    x=alt.X('earlygoldblue', scale=alt.Scale(zero=False)),
    y=alt.Y('lategoldblue', scale=alt.Scale(zero=False)),
    color='Year:O'
).interactive()


alt.Chart(...)

In [ ]:
alt.Chart(tidyleague.sample(5000)).mark_point(size=.3).encode(
    x=alt.X('earlygoldblue', scale=alt.Scale(zero=False)),
    y=alt.Y('bwin', scale=alt.Scale(zero=False)),
    color='Year:O'
).interactive()
